In [1]:
import numpy as np
import pandas as pd
from sklearn.impute import KNNImputer

## Loading data

In [2]:
pd.set_option("display.max_rows", None)
pd.set_option("display.max_colwidth", None)
pd.set_option("display.max_columns", None)

In [3]:
df = pd.read_csv("flats_set1.csv")

In [4]:
df.head(3)

price           district                     district_2     rooms   area  \
0  847 000  Kraków-Podgórze,                     Zakrzówek,   3 pokoje  52,96   
1      NaN          Dębniki,              ul. Fedorowicza 21  2 pokoje  28,30   
2  849 000    Prądnik Biały,   Andrzeja Frycza-Modrzewskiego  3 pokoje     62   

        floor  levels  bathrooms bathroom_with_toilet     market  \
0    parter/6     NaN        NaN                  NaN  Pierwotny   
1  piętro 5/5     NaN        NaN                  NaN  Pierwotny   
2  piętro 5/5     NaN        1.0                  Tak     Wtórny   

  type_of_contract    building_type building_material  year_built  \
0              NaN  Apartamentowiec            Pustak      2025.0   
1              NaN              NaN               NaN      2026.0   
2    Na wyłączność             Blok             Cegła      2000.0   

       heating kitchen_type balcony balcony_area terrace loggia garden  \
0  Co Miejskie          NaN     NaN          NaN     Tak    NaN    NaN   
1          NaN          NaN     NaN          NaN     NaN    NaN    NaN   
2          NaN       Osobna     Tak          NaN     Nie    NaN    NaN   

  windows property_condition form_of_ownership  \
0     NaN                NaN               NaN   
1     NaN                NaN               NaN   
2     NaN              Dobry          Własność   

                                                                                            advantages  \
0          ['winda', 'kuchnia otwarta', 'miejsce parkingowe', 'ogródek', 'taras', 'parking podziemny']   
1  ['balkon', 'klimatyzacja', 'miejsce parkingowe', 'ogrzewana podłoga', 'taras', 'parking podziemny']   
2                            ['balkon', 'dwustronne', 'kuchnia osobna', 'miejsce parkingowe', 'wanna']   

                                                                                                        link  
0                            https://gratka.pl/nieruchomosci/mieszkanie-krakow-debniki-kapelanka/ob/40814263  
1                       https://gratka.pl/nieruchomosci/mieszkanie-krakow-debniki-fedorowicza-21/ob/41025813  
2  https://gratka.pl/nieruchomosci/mieszkanie-krakow-pradnik-bialy-andrzeja-frycza-modrzewskiego/ob/40505385

## Data cleaning and feature engineering

All columns will be analyzed for relevance and omissions. Unnecessary columns will be removed. Additional relevant columns will be created based on existing features.

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7000 entries, 0 to 6999
Data columns (total 26 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   price                 5937 non-null   object 
 1   district              6976 non-null   object 
 2   district_2            6530 non-null   object 
 3   rooms                 7000 non-null   object 
 4   area                  7000 non-null   object 
 5   floor                 6954 non-null   object 
 6   levels                709 non-null    float64
 7   bathrooms             2924 non-null   float64
 8   bathroom_with_toilet  1946 non-null   object 
 9   market                7000 non-null   object 
 10  type_of_contract      1170 non-null   object 
 11  building_type         4935 non-null   object 
 12  building_material     3804 non-null   object 
 13  year_built            6422 non-null   float64
 14  heating               4622 non-null   object 
 15  kitchen_type         

#### Column "price"
Deleting rows where there is no price

In [6]:
df = df.dropna(subset="price").reset_index(drop= True)

In [7]:
df.price.value_counts()

price
Zarezerwow    83
699 000       83
799 000       77
599 000       70
649 000       56
650 000       50
749 000       50
899 000       47
750 000       47
999 000       41
690 000       36
729 000       30
499 000       29
630 000       28
529 000       28
550 000       27
890 000       25
660 000       25
590 000       25
620 000       25
850 000       23
739 000       23
569 000       23
1 100 000     23
639 000       23
770 000       22
1 200 000     22
760 000       22
720 000       22
719 000       22
669 000       21
740 000       21
1 250 000     21
540 000       21
870 000       20
849 000       20
950 000       20
730 000       20
1 099 000     19
980 000       19
795 000       19
1 050 000     19
695 000       19
880 000       19
949 000       19
625 000       18
520 000       18
1 450 000     18
820 000       18
900 000       18
875 000       17
549 000       17
600 000       17
530 000       17
780 000       17
829 000       17
1 299 000     17
659 000       16
680 000 

Removing columns where instead of the price there is information that the apartment is reserved.

In [8]:
df = df.drop(df[df.price == "Zarezerwow"].index)

In [9]:
df.price.value_counts()

price
699 000       83
799 000       77
599 000       70
649 000       56
749 000       50
650 000       50
899 000       47
750 000       47
999 000       41
690 000       36
729 000       30
499 000       29
529 000       28
630 000       28
550 000       27
620 000       25
890 000       25
590 000       25
660 000       25
739 000       23
1 100 000     23
850 000       23
569 000       23
639 000       23
720 000       22
719 000       22
770 000       22
760 000       22
1 200 000     22
540 000       21
1 250 000     21
740 000       21
669 000       21
849 000       20
870 000       20
950 000       20
730 000       20
695 000       19
880 000       19
795 000       19
1 050 000     19
1 099 000     19
949 000       19
980 000       19
520 000       18
1 450 000     18
900 000       18
625 000       18
820 000       18
530 000       17
1 299 000     17
829 000       17
780 000       17
600 000       17
549 000       17
875 000       17
595 000       16
990 000       16
659 000 

Remove spaces and change data type to int.

In [10]:
df.price = df.price.str.replace(" ", "")

In [11]:
df.price = df.price.astype("int64")

### Columns "district", "district_2"
The data contains two columns: "district" and "district_2". The district name should appear in the "district" column. After analysis, it was found that for some of the data, the city name "Kraków" appears instead of the district in the "district" column, and the district name is in the second column: "district_2". A new column, "district_result", will be created, which will contain the district name derived from the above-mentioned columns.

In [12]:
df[df["district"] == "Kraków, "]

price  district                                            district_2  \
4      599000  Kraków,                                              Czyżyny,    
8      700000  Kraków,                                     Czyżyny, Czyżyny,    
19     750000  Kraków,                            Bronowice, Bronowice Małe,    
25     699000  Kraków,                                    Bieżanów-Prokocim,    
27     569000  Kraków,                                            Nowa Huta,    
28     814500  Kraków,         Wzgórza Krzesławickie, Wzgórza Krzesławickie,    
29     739000  Kraków,                                    Krowodrza, Łobzów,    
30    1180189  Kraków,                               Łagiewniki, Łagiewniki,    
32     762609  Kraków,                                 Bronowice, Bronowice,    
33     754730  Kraków,                                 Bronowice, Bronowice,    
36    1560000  Kraków,                                          Środmieście,    
38     630000  Kraków,                              Stare Miasto, Kazimierz,    
41     259000  Kraków,                                              Nowa Huta   
43     569000  Kraków,                                             Podgórze,    
44    1090000  Kraków,                                                Dębniki   
56     859995  Kraków,         Wzgórza Krzesławickie, Wzgórza Krzesławickie,    
59    1000000  Kraków,                             Łagiewniki-Borek Fałęcki,    
64    1534080  Kraków,                                              Kazimierz   
66     789214  Kraków,                                 Bronowice, Bronowice,    
69     811125  Kraków,         Wzgórza Krzesławickie, Wzgórza Krzesławickie,    
72     487060  Kraków,         Wzgórza Krzesławickie, Wzgórza Krzesławickie,    
75    1450000  Kraków,                                          Zwierzyniec,    
79     874603  Kraków,                                   Podgórze, Podgórze,    
81     858614  Kraków,                         Prądnik Biały, Prądnik Biały,    
82     771258  Kraków,                               Łagiewniki, Łagiewniki,    
83    1112820  Kraków,                               Łagiewniki, Łagiewniki,    
86    1099000  Kraków,                                     Prądnik Czerwony,    
89    2200000  Kraków,                                           Grzegórzki,    
91     799000  Kraków,                                 Nowa Huta, Nowa Huta,    
92     521850  Kraków,         Wzgórza Krzesławickie, Wzgórza Krzesławickie,    
95     624000  Kraków,                                        Mistrzejowice,    
98     694035  Kraków,         Wzgórza Krzesławickie, Wzgórza Krzesławickie,    
100    521850  Kraków,         Wzgórza Krzesławickie, Wzgórza Krzesławickie,    
104    853307  Kraków,                         Prądnik Biały, Prądnik Biały,    
110    545278  Kraków,                                    Podgórze, Rybitwy,    
113    722454  Kraków,                               Łagiewniki, Łagiewniki,    
114    699000  Kraków,                                         Stare Miasto,    
115    899000  Kraków,                                             Podgórze,    
120    870000  Kraków,                                      Dębniki, Ruczaj,    
121    987525  Kraków,                                    Dębniki , Dębniki,    
122    884461  Kraków,                                 Bronowice, Bronowice,    
123    794244  Kraków,                                 Bronowice, Bronowice,    
127    799000  Kraków,                              Prądnik Czerwony, Olsza,    
130   1531700  Kraków,                                           Stare Miasto   
132    609000  Kraków,                                            Nowa Huta,    
135    900000  Kraków,                                              Dębniki,    
139    829000  Kraków,                                    Podgórze, Płaszów,    
141    690000  Kraków,                                           Stare Miasto   
142    715000  Kraków,                 

In [13]:
df["district_result"] = np.where(df["district"] ==  "Kraków, ", df["district_2"], df["district"])

District names are stored in various formats. Sometimes, instead of a district, a street or district name is provided. The "district_result" column will be mapped to contain only district names. Values that appear only once or twice will be removed.

In [14]:
df["district_result"].value_counts()

district_result
Prądnik Biały,                                          388
Stare Miasto,                                           358
Kraków-Podgórze,                                        309
Podgórze,                                               263
Kraków-Krowodrza,                                       248
Krowodrza,                                              192
Podgórze Duchackie,                                     187
Bronowice,                                              169
Łagiewniki, Łagiewniki,                                 166
Grzegórzki,                                             163
Dębniki,                                                158
Kraków-Nowa Huta,                                       152
Nowa Huta,                                              151
Kraków-Śródmieście,                                     150
Ruczaj,                                                 148
Czyżyny,                                                141
Dębniki , Dębniki,      

In [15]:
dictionary_district= {"Stare Miasto, ": "Stare Miasto",
                      "Kraków-Śródmieście, ": "Stare Miasto",
                      "Śródmieście, ": "Stare Miasto",
                      "Kazimierz, ": "Stare Miasto",
                      "Stare Miasto, Stare Miasto, ": "Stare Miasto",
                      "Stare Miasto, Kazimierz, ": "Stare Miasto",
                      "Kazimierz": "Stare Miasto",
                      "Wita Stwosza": "Stare Miasto",
                      "Środmieście, ": "Stare Miasto",
                      "Kleparz, ": "Stare Miasto",
                      "Stare Miasto (historyczne), ": "Stare Miasto",
                      "Piasek, ": "Stare Miasto",
                      "Stare Miasto, Kleparz, ": "Stare Miasto",
                      "Grzegórzki, ": "Grzegórzki",
                      "Grzegórzki, Grzegórzki, ": "Grzegórzki",
                      "Grzegórzki, Dąbie, ": "Grzegórzki",
                      "Grzegórzki, Osiedle Oficerskie, ": "Grzegórzki",
                      "Olsza, ": "Grzegórzki",
                      "Na Szaniec": "Grzegórzki",
                      "Dąbie, ": "Grzegórzki",
                      "Pilotów": "Grzegórzki",
                      "Prądnik Czerwony, ": "Prądnik Czerwony",
                      "Prądnik Czerwony, Prądnik Czerwony, ": "Prądnik Czerwony",
                      "Prądnik Czerwony, Olsza, ": "Prądnik Czerwony",
                      "Prądnik Biały, Prądnik Biały, ": "Prądnik Biały",
                      "Prądnik Biały, ": "Prądnik Biały",
                      "Azory, ": "Prądnik Biały",
                      "Górka Narodowa, ": "Prądnik Biały",
                      "Żabiniec, ": "Prądnik Biały",
                      "Prądnik Biały, Górka Narodowa, ": "Prądnik Biały",
                      "Eliasza Radzikowskiego": "Prądnik Biały",
                      "Piotra Stachiewicza": "Prądnik Biały",
                      "Pradnik Biały , Pradnik Biały, ": "Prądnik Biały",
                      "Kraków-Krowodrza, ": "Krowodrza",
                      "Krowodrza, ": "Krowodrza", 
                      "Krowodrza, Łobzów, ": "Krowodrza",
                      "Krowodrza, Azory, ": "Krowodrza",
                      "Kraków-Krowodrza": "Krowodrza",
                      "Krowodrza, Żabiniec, ": "Krowodrza",
                      "Łobzów, ": "Krowodrza",
                      "Krowodrza, Krowodrza Górka, ": "Krowodrza",
                      "Bronowice Wielkie, ": "Prądnik Biały",
                      "Bronowice, ": "Bronowice",
                      "Bronowice, Bronowice, ": "Bronowice",
                      "Bronowice, Bronowice Małe, ": "Bronowice",
                      "Bronowice Małe, ": "Bronowice",
                      "Bronowice, Mydlniki, ": "Bronowice", 
                      "Zwierzyniec, ": "Zwierzyniec",
                      "Zwierzyniec, Zwierzyniec, ": "Zwierzyniec",
                      "Wola Justowska, ": "Zwierzyniec",
                      "Salwator, ": "Zwierzyniec",
                      "Przegorzały": "Zwierzyniec",
                      "Zwierzyniec, Wola Justowska, ": "Zwierzyniec",
                      "Bielany, ": "Zwierzyniec",
                      "Ruczaj, ": "Dębniki",
                      "Dębniki, ": "Dębniki",
                      "Dębniki , Dębniki, ": "Dębniki",
                      "Dębniki, Ruczaj, ": "Dębniki",
                      "Ruczaj": "Dębniki",
                      "Ruczaj, Ruczaj, ": "Dębniki",
                      "Ludwinów, ": "Dębniki",
                      "Łagiewniki, Łagiewniki, ": "Łagiewniki-Borek Fałęcki",
                      "Łagiewniki-Borek Fałęcki, ": "Łagiewniki-Borek Fałęcki",
                      "Łagiewniki, ": "Łagiewniki-Borek Fałęcki",
                      "Borek Fałęcki, ": "Łagiewniki-Borek Fałęcki",
                      "Swoszowice, ": "Swoszowice",
                      "Kliny, ": "Swoszowice",
                      "Dębniki, Kliny, ": "Swoszowice",
                      "Swoszowice, Opatkowice, ": "Swoszowice",
                      "Opatkowice, ": "Swoszowice",
                      "Podgórze Duchackie, ": "Podgórze Duchackie",
                      "Wola Duchacka, ": "Podgórze Duchackie",
                      "Kurdwanów, ": "Podgórze Duchackie",
                      "Podgórze Duchackie, Kurdwanów, ": "Podgórze Duchackie",
                      "Wola Duchacka": "Podgórze Duchackie",
                      "Bonarka, ": "Podgórze Duchackie",
                      "Podgórze Duchackie, Wola Duchacka, ": "Podgórze Duchackie",
                      "Kurdwanów Nowy, ": "Podgórze Duchackie",
                      "Podgórze Duchackie, Piaski, ": "Podgórze Duchackie",
                      "Marii i Bolesława Wysłouchów": "Podgórze Duchackie",
                      "Bieżanów-Prokocim, ": "Bieżanów-Prokocim",
                      "Bieżanów, ": "Bieżanów-Prokocim",
                      "Bieżanów-Prokocim, Złocień, ": "Bieżanów-Prokocim",
                      "Prokocim, ": "Bieżanów-Prokocim",
                      "Bieżanów-Prokocim, Bieżanów, ": "Bieżanów-Prokocim",
                      "Wielicka": "Bieżanów-Prokocim",
                      "Bieżanów": "Bieżanów-Prokocim",
                      "Jana Kurczaba": "Bieżanów-Prokocim",
                      "Złocień, ": "Bieżanów-Prokocim",
                      "Kraków-Podgórze, ": "Podgórze",
                      "Podgórze, ": "Podgórze",
                      "Podgórze, Podgórze, ": "Podgórze",
                      "Kraków-Podgórze": "Podgórze",
                      "Zabłocie, ": "Podgórze",
                      "Przewóz, ": "Podgórze",
                      "Płaszów, ": "Podgórze",
                      "Rybitwy, ": "Podgórze",
                      "Zabłocie": "Podgórze",
                      "Podgórze, Płaszów, ": "Podgórze",
                      "Rybitwy , Rybitwy, ": "Podgórze",
                      "Podgórze, Zabłocie, ": "Podgórze",
                      "Przewóz": "Podgórze",
                      "Podgórze, Stare Podgórze, ": "Podgórze",
                      "Stare Podgórze, ": "Podgórze",
                      "Podgórze Stare, ": "Podgórze",
                      "Podgórze, Rybitwy, ": "Podgórze",
                      "Rydlówka": "Podgórze",
                      "Czyżyny, ": "Czyżyny",
                      "Czyżyny, Czyżyny, ": "Czyżyny",
                      "Osiedle Avia, ": "Czyżyny",
                      "Mistrzejowice, ": "Mistrzejowice",
                      "Mistrzejowice, Mistrzejowice, ": "Mistrzejowice",
                      "Bieńczyce, ": "Bieńczyce",
                      "Bieńczyce, Bieńczyce, ": "Bieńczyce",
                      "Wzgórza Krzesławickie, Wzgórza Krzesławickie, ": "Wzgórza Krzesławickie",
                      "Wzgórza Krzesławickie, ": "Wzgórza Krzesławickie",
                      "Kraków-Nowa Huta, ": "Nowa Huta",
                      "Nowa Huta, ": "Nowa Huta",
                      "Nowa Huta, Nowa Huta, ": "Nowa Huta",
                      "Kraków-Nowa Huta": "Nowa Huta",
                      "Branice": "Nowa Huta",
                      "Branice, ": "Nowa Huta"
                                                   }

In [16]:
df["district_result"] = df.district_result.replace(dictionary_district)

In [17]:
df["district_result"].value_counts()

district_result
Podgórze                                                908
Stare Miasto                                            695
Prądnik Biały                                           578
Dębniki                                                 494
Krowodrza                                               483
Nowa Huta                                               360
Bronowice                                               316
Podgórze Duchackie                                      284
Łagiewniki-Borek Fałęcki                                209
Grzegórzki                                              209
Bieżanów-Prokocim                                       196
Czyżyny                                                 177
Prądnik Czerwony                                        157
Zwierzyniec                                             121
Wzgórza Krzesławickie                                   116
Bieńczyce                                               101
Mistrzejowice           

In [18]:
df = df[df["district_result"].isin(dictionary_district.values())]

The distance.csv file contains approximate distances of individual districts from the city center.

A property's distance from the city center can impact its price. We don't have the exact location of the property, so we'll use the districts' distances from the center and create an additional column: "distance_from_center".

In [19]:
distance = pd.read_csv('distance.csv')
distance

Stare Miasto  Grzegórzki  Prądnik Czerwony  Prądnik Biały  Krowodrza  \
0           0.4        1.15               2.7            3.6        1.6   

   Bronowice  Zwierzyniec  Dębniki  Łagiewniki-Borek Fałęcki  Swoszowice  \
0        5.5          5.4      4.5                       3.5         5.6   

   Podgórze Duchackie  Bieżanów-Prokocim  Podgórze  Czyżyny  Mistrzejowice  \
0                 4.0                7.5       3.6      5.2            5.6   

   Bieńczyce  Wzgórza Krzesławickie  Nowa Huta  
0        5.9                   10.8       12.9

In [20]:
distance_dict = distance.to_dict('records')

In [21]:
df["distance_from_center"] = df.district_result.map(distance_dict[0])

In [22]:
df.distance_from_center.value_counts().sort_values()

distance_from_center
5.90      101
10.80     116
5.40      121
5.60      142
2.70      157
5.20      177
7.50      196
3.50      209
1.15      209
4.00      284
5.50      316
12.90     360
1.60      483
4.50      494
0.40      695
3.60     1486
Name: count, dtype: int64

In [23]:
df = df.drop(["district", "district_2"], axis=1) #Removing unnecessary columns

### Column "rooms"

In [24]:
df["rooms"].value_counts()

rooms
2 pokoje      2193
3 pokoje      1909
4 pokoje       679
1 pokój        587
5 pokoi        122
6 pokoi         39
7 pokoi          5
8 pokoi          3
 65,75 m²        1
12 pokoi         1
 98 m²           1
 49,71 m²        1
22 pokoje        1
 57,50 m²        1
 15,90 m²        1
 79 m²           1
 67 m²           1
Name: count, dtype: int64

The values in the "rooms" column incorrectly include square footage, so those rows will be deleted. The remaining values are the number of rooms, ranging from 1 to 8, and two outliers: 12 and 22. The apartments don't have that many rooms, so values 12 and 22 will be deleted (probably incorrectly entered values).

In [25]:
rooms_dict = {"1 pokój": "1",
              "2 pokoje": "2",
              "3 pokoje": "3",
              "4 pokoje": "4",
              "5 pokoi": "5",
              "6 pokoi": "6",
              "7 pokoi": "7",
              "8 pokoi": "8"
             }

In [26]:
df["rooms"] = df["rooms"].map(rooms_dict)

In [27]:
df = df.dropna(subset="rooms").reset_index(drop= True)

In [28]:
df["rooms"] = df["rooms"].astype("int")

### Column "area" 
Changing comma to dot and changing column to float.

In [29]:
df["area"] = df["area"].apply(lambda x: str(x.replace(",", ".")))

In [30]:
df["area"] = df["area"].astype("float")

### Column "floor"
Remove the null values in the "floor" column and split the column into the property's floor number and the number of floors in the building where the property is located. The building's floor number is irrelevant, so it will be removed.

In [31]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5537 entries, 0 to 5536
Data columns (total 26 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   price                 5537 non-null   int64  
 1   rooms                 5537 non-null   int32  
 2   area                  5537 non-null   float64
 3   floor                 5503 non-null   object 
 4   levels                678 non-null    float64
 5   bathrooms             2756 non-null   float64
 6   bathroom_with_toilet  1869 non-null   object 
 7   market                5537 non-null   object 
 8   type_of_contract      1090 non-null   object 
 9   building_type         4679 non-null   object 
 10  building_material     3612 non-null   object 
 11  year_built            5019 non-null   float64
 12  heating               4378 non-null   object 
 13  kitchen_type          3833 non-null   object 
 14  balcony               3524 non-null   object 
 15  balcony_area         

In [32]:
df = df.dropna(subset="floor").reset_index(drop= True)

In [33]:
df["floor"].value_counts(dropna=False)

floor
piętro 4/4      301
parter/4        293
piętro 3/4      293
piętro 2/4      261
piętro 1/3      260
piętro 1/4      260
parter/3        238
piętro 3/3      238
piętro 2/3      220
parter/2        199
piętro 1/2      184
piętro 1/5      172
piętro 4/5      149
piętro 2/2      134
parter/5        133
piętro 2/5      115
piętro 3/5      107
piętro 5/5      102
piętro 1/6       89
piętro 4         75
piętro 1/7       72
piętro 2/6       69
parter/1         66
piętro 4/6       65
piętro 6/6       64
piętro 3/6       63
piętro 5/6       59
piętro 3         56
piętro 5/10      49
piętro 1/1       47
piętro 5         42
piętro 3/7       39
piętro 2         39
piętro 1/10      38
parter           36
piętro 2/7       35
piętro 6/7       35
piętro 1         34
piętro 7/10      33
piętro 2/10      33
parter/10        32
piętro 4/7       32
parter/6         32
piętro 9/10      32
piętro 4/10      30
piętro 3/10      30
piętro 6         27
piętro 7/7       26
piętro 8/10      26
piętro 5/7    

In [34]:
df[["floor_of_flat", "floor_of_bulding"]] = df["floor"].str.split("/", expand= True)

Mapping the number of floors from -1 to 16. The ground floor will be mapped as 0.

In [35]:
df.floor_of_flat.value_counts()

floor_of_flat
piętro 1     1199
parter       1076
piętro 2      931
piętro 3      864
piętro 4      675
piętro 5      295
piętro 6      158
piętro 7      112
piętro 8       53
piętro 9       49
piętro 10      47
piętro 11      16
piętro -1      11
piętro 14       6
piętro 15       5
piętro 12       4
piętro 13       2
Name: count, dtype: int64

In [36]:
floor_dict = {"piętro -1": -1,
              "parter": 0
             }
for i in range(1,16):
    floor_dict[f"piętro {i}"] = i
    

In [37]:
df.floor_of_flat = df.floor_of_flat.map(floor_dict)

In [38]:
df = df.drop(["floor", "floor_of_bulding"], axis=1) #Removing unnecessary columns

### Columns: "levels", "bathrooms", "bathroom_with_toilet", "type of contract", "windows"
Columns will be removed because they have many gaps, errors or do not have a significant impact on the price of the apartment.

In [39]:
df["levels"].value_counts(dropna=False)

levels
NaN    4829
1.0     529
2.0     132
3.0       7
5.0       4
4.0       2
Name: count, dtype: int64

In [40]:
df["bathrooms"].value_counts(dropna=False)

bathrooms
NaN      2757
1.0      2424
2.0       301
3.0        16
4.0         2
6.0         1
21.0        1
127.0       1
Name: count, dtype: int64

In [41]:
df["bathroom_with_toilet"].value_counts(dropna=False)

bathroom_with_toilet
NaN    3643
Tak    1710
Nie     150
Name: count, dtype: int64

In [42]:
df["type_of_contract"].value_counts(dropna=False) 

type_of_contract
NaN              4416
Na wyłączność    1087
Name: count, dtype: int64

In [43]:
df["windows"].value_counts(dropna=False)

windows
NaN                                    3371
PCV                                    1787
PCV 3 szyby, ciepły montaż               63
PCV 3 komorowe                           55
DREWNIANE NOWY TYP                       44
Drewniane                                41
Nowe PCV                                 38
Drewniane nowe                           20
PCV, DREWNIANE STARY TYP                 14
Nowe drewniane                           10
Częściowo wymienione                     10
Nowe plastikowe                           8
Nowe                                      7
Aluminiowe                                7
DREWNIANE STARY TYP                       7
PLASTIKOWE                                5
Aluminium                                 4
Aluminiowe 3 szybowe, ciepły montaż       3
Pcv                                       3
Inne                                      2
Drewniane stare                           2
Połaciowe                                 2
Name: count, dtype: int6

In [44]:
df = df.drop(["levels", "bathrooms", "bathroom_with_toilet", "type_of_contract", "windows"], axis=1)

### Column "building_type"
Building type will be mapped to 6 categories. Missing data and other types will be mapped to "Other/No data".

In [45]:
df["building_type"].value_counts(dropna=False)

building_type
Blok                     1459
NaN                       854
Apartamentowiec           726
Kamienica                 424
Blok Mieszkalny           399
APARTAMENTOWIEC           346
NISKI BLOK                303
Nowe budownictwo          234
BLOK                      207
KAMIENICA                 146
WIEŻOWIEC                 105
Budynek wielorodzinny      46
MIESZKALNO-BIUROWY         35
NISKI WIELORODZINNY        31
Wieżowiec                  25
Dom Wielorodzinny          21
Bliźniak                   20
Szeregowiec                17
Blok mieszkalny            14
SEGMENT                    13
Dom wielorodzinny          11
Szeregowy                  11
DOM                        10
Budynek wolnostojący        6
Inna                        6
Wolnostojący                5
Segment Skrajny             5
Inny                        4
Segment                     3
Historyczny/Zabytkowy       2
Dom wolnostojący            2
Kamienica luksusowa         2
Niski wielorodzinny       

In [46]:
building_type_dict = {"Blok Mieszkalny": "Apartment building",
                      "Blok": "Apartment building",
                      "Blok mieszkalny": "Apartment building",
                      "BLOK": "Apartment building",
                      "NISKI BLOK": "Apartment building",
                      "WIEŻOWIEC": "Apartment building",
                      "Wieżowiec": "Apartment building",
                      "APARTAMENTOWIEC": "Apartment building",
                      "Apartamentowiec": "Apartment building",
                      "KAMIENICA": "Tenement",
                      "Kamienica luksusowa": "Tenement",
                      "Kamienica": "Tenement",
                      "Dom wielorodzinny": "Multi-family building",
                      "Dom Wielorodzinny": "Multi-family building",
                      "NISKI WIELORODZINNY": "Multi-family building",
                      "Niski wielorodzinny": "Multi-family building",
                      "Budynek dwurodzinny": "Multi-family building",
                      "Szeregowy": "Multi-family building",
                      "SEGMENT": "Multi-family building",
                      "Segment": "Multi-family building",
                      "Segment Skrajny": "Multi-family building",
                      "Segment Środkowy": "Multi-family building",
                      "Półbliźniak": "Multi-family building", 
                      "Szeregowiec": "Multi-family building",
                      "Bliźniak": "Multi-family building",
                      "Budynek wielorodzinny": "Multi-family building",
                      "CZĘŚĆ DOMU": "Detached house",
                      "Piętro domu": "Detached house",
                      "DOM": "Detached house",
                      "Dom": "Detached house",
                      "Dom jednorodzinny": "Detached house",
                      "Dom wolnostojący": "Detached house",
                      "Budynek wolnostojący": "Detached house",
                      "Wolnostojący": "Detached house",
                      "Nowe budownictwo": "New construction",
                      "Inna": "Other/ No data",
                      "INNY": "Other/ No data",
                      "-": "Other/ No data",
                      "Rezydencja": "Other/ No data",
                      "Historyczny/Zabytkowy": "Other/ No data",
                      "BUDYNEK BIUROWY": "Other/ No data",
                      "MIESZKALNO-BIUROWY": "Other/ No data",
                      "Inny": "Other/ No data",
                      "Biurowiec": "Other/ No data",
                      "LOFT": "Other/ No data"
}

In [47]:
df["building_type"] = df.building_type.replace(building_type_dict)

In [48]:
df["building_type"].value_counts(dropna=False)

building_type
Apartment building       3584
NaN                       854
Tenement                  572
New construction          234
Multi-family building     183
Other/ No data             51
Detached house             25
Name: count, dtype: int64

In [49]:
df["building_type"] = df["building_type"].fillna("Other/ No data") #Filling in the missing data

In [50]:
df["building_type"].value_counts(dropna=False)

building_type
Apartment building       3584
Other/ No data            905
Tenement                  572
New construction          234
Multi-family building     183
Detached house             25
Name: count, dtype: int64

### Column "building material"
Building material will be mapped to 6 categories. Missing data will be mapped to "No data".

In [51]:
df["building_material"].value_counts(dropna=False)

building_material
NaN                                                1901
Cegła                                               580
Beton, cegła                                        365
Pustak                                              300
CEGŁA                                               259
Mieszana                                            256
MIESZANY                                            240
Wielka płyta                                        154
Rama H                                              145
Beton, płyta                                        142
Płyta                                                96
WIELKA PŁYTA                                         81
PUSTAK                                               81
YTong                                                80
BETON                                                77
-                                                    72
Zróżnicowany                                         71
INNY                          

In [52]:
building_material_dict = {"CEGŁA": "Brick",
                          "Cegła": "Brick",
                          "Cegła ceramiczna": "Brick",
                          "PUSTAK": "Brick",
                          "Pustak": "Brick",
                          "YTong": "Brick",
                          "Tradycyjna": "Brick",
                          "Ceramika": "Brick",
                          "CERAMIKA": "Brick",
                          "Ceramiczny Porotherm": "Brick",
                          "Cegła, pustak": "Brick",
                          "Pustak ceramiczny": "Brick",
                          "Ceramiczny porotherm": "Brick",
                          "Cegła + styropian": "Brick",
                          "Cegła nowa": "Brick",
                          "Cegła, prefabrykat, pustak": "Brick",
                          "Cegła czerwona": "Brick",
                          "Bloczki": "Brick",
                          "YTONG": "Brick",
                          "Tradycyjna murowana": "Brick",
                          "Cegła stara": "Brick",
                          "Murowana": "Brick",
                          "Stara cegła": "Brick",
                          "Pustak i cegła": "Brick",
                          "Porotherm": "Brick",
                          "SILIKAT": "Brick",
                          "Bloczki ytong": "Brick",
                          "GAZOBETON": "Brick",
                          "MUROWANA": "Brick",
                          "BLOCZKI": "Brick",
                          "Gazobeton": "Brick",
                          "Pustak max": "Brick",
                          "Beton, gazobeton": "Brick",
                          "Kamienica": "Brick",
                          "Beton komórkowy": "Brick",
                          "Nowa cegła": "Brick",
                          "Silikat": "Brick",
                          "Suporex": "Brick",
                          "Prefabrykat, pustak": "Brick",
                          "Nowe budownictwo, blok, z 2017 roku, pustak cerami": "Brick",
                          "MIESZANY": "Mixed construction, other",
                          "Mieszana": "Mixed construction, other",
                          "Beton, cegła": "Mixed construction, other",
                          "Kon. szkieletowa": "Mixed construction, other",
                          "Technologia kanadyjska": "Mixed construction, other",
                          "Zróżnicowany": "Mixed construction, other",
                          "INNY": "Mixed construction, other",
                          "Inna": "Mixed construction, other",
                          "Inne": "Mixed construction, other",
                          "Konstrukcja mieszana": "Mixed construction, other",
                          "Inny": "Mixed construction, other",
                          "Płyta": "Large slab",
                          "WIELKA PŁYTA": "Large slab",
                          "Wielka płyta": "Large slab",
                          "WIELKOPŁYTOWA": "Large slab",
                          "Blok z lat 70-tych, technologia wielkiego bloku": "Large slab",
                          "Beton, ocieplony, płyta": "Large slab",
                          "Blok, blok z lat 70-tych": "Large slab",
                          "Blok z lat 60-tych": "Large slab",
                          "Z lat 80-tych": "Large slab",
                          "Blok, z lat 80-tych": "Large slab",
                          "Płyta warstwowa": "Large slab",
                          "Płyta po termomodernizacji": "Large slab",
                          "Konstrukcja żelbetowa": "Concrete, reinforced concrete",
                          "BETON": "Concrete, reinforced concrete",
                          "Beton, płyta": "Concrete, reinforced concrete",
                          "Beton": "Concrete, reinforced concrete",
                          "żelbeton": "Concrete, reinforced concrete",
                          "-": "No data",
                          "Mieszkanie": "No data",
                          "Blok, z lat 50-tych": "No data",
                          "Rama h": "H-frame",
                          "Rama H": "H-frame",
                          "RAMA H": "H-frame"                
}

In [53]:
df["building_material"] = df.building_material.replace(building_material_dict)

In [54]:
df["building_material"].value_counts(dropna=False)

building_material
NaN                              1901
Brick                            1589
Mixed construction, other        1059
Large slab                        382
Concrete, reinforced concrete     336
H-frame                           163
No data                            73
Name: count, dtype: int64

In [55]:
df["building_material"] = df["building_material"].fillna("No data") #Filling in the missing data

In [56]:
df["building_material"].value_counts(dropna=False)

building_material
No data                          1974
Brick                            1589
Mixed construction, other        1059
Large slab                        382
Concrete, reinforced concrete     336
H-frame                           163
Name: count, dtype: int64

### Column "market"
The "market" column has two categories and no missing data, but there are errors. Grouping the property's construction year by market type reveals that the primary market includes years that indicate a secondary market (even years dating back to the 19th century). Therefore, for building years older than 2012, the market category was changed from primary to secondary.

In [57]:
df.market.value_counts(dropna=False)

market
Wtórny       3519
Pierwotny    1984
Name: count, dtype: int64

In [58]:
market_dict = {"Pierwotny": "Primary",
               "Wtórny": "Secondary"
}

In [59]:
df["market"] = df.market.replace(market_dict)

In [60]:
df.market.value_counts(dropna=False)

market
Secondary    3519
Primary      1984
Name: count, dtype: int64

In [61]:
df.groupby(["market"])["year_built"].value_counts(dropna=False)

market     year_built
Primary    2026.0        668
           2025.0        643
           2024.0        383
           2027.0        136
           2023.0         73
           NaN            41
           2022.0         11
           1890.0          4
           1911.0          4
           1928.0          3
           2020.0          3
           1899.0          2
           1930.0          2
           2004.0          2
           1905.0          1
           1907.0          1
           1965.0          1
           1970.0          1
           1980.0          1
           2007.0          1
           2010.0          1
           2012.0          1
           2019.0          1
Secondary  NaN           468
           2024.0        215
           1980.0        167
           1970.0        158
           2023.0        118
           2018.0        107
           2017.0         93
           2019.0         87
           2022.0         81
           2021.0         76
           1960.0    

In [62]:
df.loc[df.year_built <2012, "market"] = df.loc[df.year_built <2012, "market"].apply(lambda x: x.replace("Primary", "Secondary"))

In [63]:
df.groupby(["market"])["year_built"].value_counts(dropna=False)

market     year_built
Primary    2026.0        668
           2025.0        643
           2024.0        383
           2027.0        136
           2023.0         73
           NaN            41
           2022.0         11
           2020.0          3
           2012.0          1
           2019.0          1
Secondary  NaN           468
           2024.0        215
           1980.0        168
           1970.0        159
           2023.0        118
           2018.0        107
           2017.0         93
           2019.0         87
           2022.0         81
           2021.0         76
           1960.0         71
           2020.0         60
           2009.0         58
           2016.0         57
           2008.0         55
           2025.0         54
           1950.0         53
           2006.0         52
           2000.0         50
           1975.0         49
           2015.0         47
           2004.0         46
           2012.0         45
           2001.0    

### Column "year_built"
The "year_built" column contains two outliers, 1400 and 1590, so all rows younger than 1800 will be removed from the column (buildings older than 1800 are unlikely to exist).
Missing data will be filled in via KNNImputer.

In [64]:
df.year_built.describe()

count    4994.000000
mean     2001.932920
std        35.639854
min      1400.000000
25%      1982.000000
50%      2020.000000
75%      2025.000000
max      2027.000000
Name: year_built, dtype: float64

In [65]:
df.year_built.sort_values()

1490    1400.0
2693    1590.0
2336    1801.0
1893    1801.0
3516    1814.0
3584    1830.0
5463    1836.0
70      1840.0
2578    1873.0
3425    1875.0
2062    1875.0
792     1878.0
88      1880.0
3841    1881.0
4923    1881.0
1559    1882.0
2603    1882.0
4291    1882.0
3967    1883.0
946     1886.0
4502    1886.0
5354    1886.0
4863    1886.0
480     1887.0
2574    1887.0
3602    1887.0
1474    1887.0
1658    1887.0
824     1887.0
4567    1888.0
5488    1889.0
5115    1890.0
858     1890.0
227     1890.0
668     1890.0
241     1890.0
4175    1890.0
530     1890.0
3555    1890.0
4242    1890.0
849     1890.0
5185    1890.0
2746    1890.0
5262    1890.0
1038    1890.0
4427    1890.0
132     1890.0
1524    1890.0
4870    1890.0
2808    1890.0
170     1890.0
2119    1890.0
4597    1890.0
1800    1890.0
3604    1890.0
2323    1890.0
4744    1890.0
2097    1890.0
4102    1890.0
3917    1891.0
193     1891.0
3728    1891.0
3374    1892.0
4684    1892.0
2975    1892.0
3445    1892.0
3923    18

In [66]:
df = df.drop(df[df.year_built < 1800].index).reset_index(drop= True)

In [67]:
knn_imputer = KNNImputer(n_neighbors=5)

In [68]:
df.year_built = knn_imputer.fit_transform(df[["year_built"]]) #Filling in the missing data

In [69]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5501 entries, 0 to 5500
Data columns (total 21 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   price                 5501 non-null   int64  
 1   rooms                 5501 non-null   int32  
 2   area                  5501 non-null   float64
 3   market                5501 non-null   object 
 4   building_type         5501 non-null   object 
 5   building_material     5501 non-null   object 
 6   year_built            5501 non-null   float64
 7   heating               4371 non-null   object 
 8   kitchen_type          3822 non-null   object 
 9   balcony               3499 non-null   object 
 10  balcony_area          1025 non-null   object 
 11  terrace               896 non-null    object 
 12  loggia                109 non-null    object 
 13  garden                35 non-null     object 
 14  property_condition    3902 non-null   object 
 15  form_of_ownership    

### Column "heating"
Heating type will be mapped to 7 categories. Missing data and other types will be mapped to "Other/No data."

In [70]:
df["heating"].value_counts(dropna=False)

heating
NaN                                          1130
C.O. miejskie                                1041
Miejskie                                     1004
C.O. Z SIECI MIEJSKIEJ                        957
Co Miejskie                                   466
C.O. GAZOWE                                   197
Gazowe                                        187
Centralne                                      81
Piec dwufunkcyjny                              65
C.O. WŁASNE                                    53
Elektryczne                                    51
Pompa ciepła                                   43
C.O. lokalne                                   39
C.O. ELEKTRYCZNE                               23
Inne                                           22
C.O. GAZOWE,C.O. WŁASNE                        21
Podłogowe                                      20
Własne dla budynku                             13
Co. z własnej kotłowni                         12
Pompa Ciepła                              

In [71]:
heating_dict = {"Miejskie": "Central city heating",
                "C.O. Z SIECI MIEJSKIEJ": "Central city heating",
                "C.O. miejskie": "Central city heating",
                "Co Miejskie": "Central city heating",
                "Co miejskie": "Central city heating",
                "C.o z sieci miejskiej": "Central city heating",
                "C.O. GAZOWE": "Gas heating",
                "C.O. GAZOWE,C.O. WŁASNE": "Gas heating",
                "Własne gazowe": "Gas heating",
                "Piec dwufunkcyjny": "Gas heating",
                "Piec gazowy dwufunkcyjny": "Gas heating",
                "Własne gazowe – piec II funkcyjny": "Gas heating",
                "Gazowe": "Gas heating",
                "Pompa Ciepła": "Heat pump",
                "POMPA CIEPŁA": "Heat pump",
                "Pompa ciepła": "Heat pump",
                "C.O. WŁASNE,POMPA CIEPŁA": "Heat pump",
                "C.O. WŁASNE": "Own/ local central heating",
                "C.O. lokalne": "Own/ local central heating",
                "Co. z własnej kotłowni": "Own/ local central heating",
                "Co Własne": "Own/ local central heating",
                "Własne dla budynku": "Own/ local central heating",
                "Piecowe": "Own/ local central heating",
                "Kotłownia": "Own/ local central heating",
                "Kotłownia lokalna": "Own/ local central heating",
                "PIEC": "Own/ local central heating",
                "Piec": "Own/ local central heating",
                "C.O. OLEJOWE,C.O. WŁASNE": "Own/ local central heating",
                "C.O. ELEKTRYCZNE": "Electric heating",
                "C.O. ELEKTRYCZNE,C.O. WŁASNE": "Electric heating",
                "Własne elektryczne": "Electric heating",
                "C.O. ELEKTRYCZNE,PIEC": "Electric heating",
                "Elektryczne": "Electric heating",
                "C.O. ELEKTRYCZNE,PROMIENNIKI PODCZERWIENI": "Electric heating", 
                "Centralne ogrzewanie": "Central heating",
                "Centralne": "Central heating",
                "Inne": "Other/ no data",
                "Inna": "Other/ no data",
                "INNE": "Other/ no data", 
                "C.O. ELEKTRYCZNE,C.O. GAZOWE": "Other/ no data",
                "Miejskie plus piecyk gazowy": "Other/ no data",
                "Klimatyzowane": "Other/ no data",
                "C.O. ELEKTRYCZNE,C.O. Z SIECI MIEJSKIEJ": "Other/ no data",
                "Geotermika": "Other/ no data",
                "C.O. WŁASNE,C.O. Z SIECI MIEJSKIEJ": "Other/ no data",
                "Podłogowe": "Other/ no data"
                
}

In [72]:
df.heating = df.heating.replace(heating_dict)

In [73]:
df["heating"].value_counts(dropna=False)

heating
Central city heating          3476
NaN                           1130
Gas heating                    473
Own/ local central heating     124
Electric heating                87
Central heating                 83
Other/ no data                  65
Heat pump                       63
Name: count, dtype: int64

In [74]:
df.heating = df.heating.fillna("Other/ no data") #Filling in the missing data

In [75]:
df["heating"].value_counts(dropna=False)

heating
Central city heating          3476
Other/ no data                1195
Gas heating                    473
Own/ local central heating     124
Electric heating                87
Central heating                 83
Heat pump                       63
Name: count, dtype: int64

### Column "kitchen_type"
The kitchen type will be mapped to 5 categories.
Additionally, the "advantages" column also contains information about the kitchen type in a given apartment. This information will be extracted and added to the kitchen column.
Missing data and other types will be mapped to "Other/No data."

In [76]:
df["kitchen_type"].value_counts(dropna=False)

kitchen_type
NaN                                                   1679
Aneks kuchenny - połączony z salonem                   781
ANEKS KUCHENNY                                         583
Aneks                                                  389
Aneks kuchenny - połączony z jadalnią                  296
ODDZIELNA                                              233
Jasna z oknem                                          226
Aneks kuchenny                                         212
Osobna                                                 206
OTWARTA                                                192
Zamknięta                                              184
Oddzielna                                              161
Z OKNEM                                                 72
Otwarta                                                 66
Widna                                                   50
Oddzielna i widna                                       32
Jasna                                      

In [77]:
kitchen_dict = {"Aneks kuchenny - połączony z salonem": "Kitchenette",
                "ANEKS KUCHENNY": "Kitchenette",
                "Aneks kuchenny": "Kitchenette",
                "Aneks": "Kitchenette",
                "Aneks kuchenny - połączony z jadalnią": "Kitchenette",
                "Aneks kuchenny – połączony z salonem ": "Kitchenette",
                "Otwarta": "Kitchenette",
                "OTWARTA": "Kitchenette",
                "W aneksie": "Kitchenette",
                "Połączona z salonem": "Kitchenette",
                "Otwarta połączona z jadalnią": "Kitchenette",
                "Z OKNEM,ANEKS KUCHENNY": "Kitchenette",
                "Kuchnia z jadalnią z wyjściem na taras": "Kitchenette",
                "Aneks kuchenny – połączony z salonem": "Kitchenette",
                "Aneks kuchenny – połączony z jadalnią": "Kitchenette",
                "Aneks w salonie": "Kitchenette",
                "W przedpokoju": "Kitchenette",
                "Wnęka": "Kitchenette",
                "Wnęka w przedpokoju": "Kitchenette",
                "POŁĄCZONA Z JADALNIĄ,Z OKNEM": "Kitchenette",
                "ODDZIELNA": "Separate kitchen",
                "Oddzielna": "Separate kitchen",
                "Osobna": "Separate kitchen",
                "Zamknięta": "Separate kitchen",
                "Oddzielna widna": "Separate kitchen",
                "Oddzielna i widna": "Separate kitchen",
                "Do własnej aranżacji, do wykończenia, oddzielna": "Separate kitchen",
                "Oddzielna, prostokątna, sprzęt AGD, umeblowana, us": "Separate kitchen",
                "Jasna, oddzielna, piecyk gazowy, kuchenka gazowo-e": "Separate kitchen",
                "Z OKNEM,ODDZIELNA": "Separate kitchen",
                "Oddzielna, jasna": "Separate kitchen",
                "ODDZIELNA,POŁĄCZONA Z JADALNIĄ": "Separate kitchen",
                "Z OKNEM": "Bright kitchen",
                "Widna": "Bright kitchen",
                "Jasna": "Bright kitchen",
                "Jasna z oknem": "Bright kitchen",
                "Widna - wejście z przedpokoju": "Bright kitchen",
                "Widna - wejście z pokoju": "Bright kitchen",
                "Jasna, meble na wymiar, otwarta na przedpokój, spr": "Bright kitchen",
                "BEZ OKNA": "Dark/ semi-open kitchen",
                "Oddzielna ciemna": "Dark/ semi-open kitchen",
                "Oddzielna i ciemna": "Dark/ semi-open kitchen",
                "Prześwit": "Dark/ semi-open kitchen",
                "OKNO NA POKÓJ": "Dark/ semi-open kitchen",
                "Z oknem do pokoju": "Dark/ semi-open kitchen",
                "Ciemna": "Dark/ semi-open kitchen",
                "Półotwarta": "Dark/ semi-open kitchen",
                "Inna": "Other/ no data",
                "Brak": "Other/ no data",
                "Meble, okap, umeblowana, ustawna, z wyjściem na ba": "Other/ no data"  
}

In [78]:
df.kitchen_type = df.kitchen_type.replace(kitchen_dict)

In [79]:
df["kitchen_type"].value_counts(dropna=False)

kitchen_type
Kitchenette                2556
NaN                        1679
Separate kitchen            832
Bright kitchen              372
Dark/ semi-open kitchen      55
Other/ no data                7
Name: count, dtype: int64

In [80]:
df.advantages.value_counts()

advantages
[]                                                                                                                                                                                                                                             175
['dla osób z niepełnosprawnością', 'komórka lokatorska', 'winda', 'balkon', 'kuchnia otwarta', 'miejsce parkingowe', 'osiedle zamknięte', 'parking podziemny']                                                                                 117
['balkon', 'kuchnia otwarta']                                                                                                                                                                                                                   71
['balkon', 'kuchnia osobna', 'miejsce parkingowe', 'parking podziemny']                                                                                                                                                                         68
['winda', 'balkon

Index lists have been created for each kitchen type (open, separate, and bright kitchen). For these apartments, the "kitchen" column will be updated with the appropriate values.

In [81]:
kitchen_open_index = []
for i in range(len(df["advantages"])):
    if 'kuchnia otwarta' in df["advantages"][i]:
        kitchen_open_index.append(i)

In [82]:
kitchen_close_index = []
for i in range(len(df["advantages"])):
    if 'kuchnia osobna' in df["advantages"][i]:
        kitchen_close_index.append(i)

In [83]:
kitchen_light_index = []
for i in range(len(df["advantages"])):
    if 'widna kuchnia' in df["advantages"][i]:
        kitchen_light_index.append(i)

For some apartments, there is a discrepancy, as the "advantages" column contains information about both open and separate kitchens. Therefore, these apartments will not have the updated "kitchen" column.

In [84]:
list_discrepancy = list(set(kitchen_close_index).intersection(set(kitchen_open_index))) 

In [85]:
list_close_kitchen = list(set(kitchen_close_index).difference(set(kitchen_open_index))) #Difference between the index sets for closed and open kitchens

In [86]:
df.loc[list_close_kitchen, "kitchen_type"] = df.loc[list_close_kitchen, "kitchen_type"].fillna("Separate kitchen")

In [87]:
list_open_kitchen = list(set(kitchen_open_index).difference(set(kitchen_close_index))) #Difference between the index sets for open and closed kitchens

In [88]:
df.loc[list_open_kitchen, "kitchen_type"] = df.loc[list_open_kitchen, "kitchen_type"].fillna("Kitchenette")

In [89]:
list_light_kitchen = list(set(kitchen_light_index).difference(list_discrepancy))

In [90]:
df.loc[list_light_kitchen, "kitchen_type"] = df.loc[list_light_kitchen, "kitchen_type"].fillna("Bright kitchen")

In [91]:
df.kitchen_type.value_counts(dropna=False)

kitchen_type
Kitchenette                3349
Separate kitchen           1009
NaN                         694
Bright kitchen              387
Dark/ semi-open kitchen      55
Other/ no data                7
Name: count, dtype: int64

In [92]:
df.kitchen_type = df.kitchen_type.fillna("Other/ no data") #Filling in the missing data

In [93]:
df.kitchen_type.value_counts(dropna=False)

kitchen_type
Kitchenette                3349
Separate kitchen           1009
Other/ no data              701
Bright kitchen              387
Dark/ semi-open kitchen      55
Name: count, dtype: int64

### Columns "balcony", "balcony_area", "loggia", "terrace", "garden"
The columns "balcony", "balcony_area", "loggia", "terrace", "garden" will be combined into one column, which will contain information whether the apartment has any of the above-mentioned amenities.

In the "balcony_area" and "garden" columns, all non-empty cells with area have the value "Tak".

In [94]:
df.loc[df["balcony_area"].dropna().index, "balcony_area"] = df.loc[df["balcony_area"].dropna().index, "balcony_area"].apply(lambda x: "Tak")

In [95]:
df["balcony_area"].value_counts()

balcony_area
Tak    1025
Name: count, dtype: int64

In [96]:
df["garden"].value_counts()

garden
30 m²        2
20 m²        2
40 m²        2
28,37 m²     2
17,16 m²     1
22,28 m²     1
9,15 m²      1
5,17 m²      1
32,39 m²     1
400 m²       1
35 m²        1
32,44 m²     1
22,23 m²     1
22 m²        1
16,55 m²     1
70 m²        1
16 m²        1
16,77 m²     1
104 m²       1
29,31 m²     1
125 m²       1
24,15 m²     1
50 m²        1
23 m²        1
155,79 m²    1
100 m²       1
137,22 m²    1
28 m²        1
123 m²       1
33 m²        1
29 m²        1
Name: count, dtype: int64

In [97]:
df.loc[df["garden"].dropna().index, "garden"] = df.loc[df["garden"].dropna().index, "garden"].apply(lambda x: "Tak")

In [98]:
df["garden"].value_counts()

garden
Tak    35
Name: count, dtype: int64

In [99]:
df["terrace"].value_counts()

terrace
Tak    578
Nie    318
Name: count, dtype: int64

In [100]:
df["balcony"].value_counts()

balcony
Tak    3298
Nie     201
Name: count, dtype: int64

In [101]:
df["loggia"].value_counts()

loggia
Tak    109
Name: count, dtype: int64

Empty cells have been filled with the value "No_data".

In [102]:
list_balcony_columns = ["balcony", "balcony_area", "terrace", "loggia", "garden"]
for i in list_balcony_columns:
    df[i] = df[i].apply(lambda x: x).fillna("No_data")

In [103]:
df["garden"].value_counts()

garden
No_data    5466
Tak          35
Name: count, dtype: int64

The "balcony", "balcony_area", "loggia", "terrace", and "garden" columns have been combined into a single column. The value "Yes" has been entered where "Tak" was entered in any column. "No_data" has been entered where all missing data was entered. In all other cases, the value "No" has been entered.

In [104]:
df["balconies"] = df["loggia"] + df["terrace"] + df["balcony"] + df["balcony_area"] + df["garden"]

In [105]:
def balconies_f(balconies):
    if "Tak" in balconies:
        return "Yes"
    elif "No_dataNo_dataNo_dataNo_dataNo_data" in balconies:
        return "No_data"
    else:
        return "No"

In [106]:
df["balconies"] = df["balconies"].apply(balconies_f)

In [107]:
df["balconies"].value_counts()

balconies
Yes        3653
No_data    1704
No          144
Name: count, dtype: int64

Furthermore, the "advantages" column also contains information about whether the apartment has a balcony, terrace, loggia, or garden. This information will be extracted and added to the "balconies" column.

In [108]:
index_list = []
balconies_list = ["balkon", "taras", "loggia", "ogródek"]
for i in range(len(df["advantages"])):
    for j in balconies_list:
        if j in df["advantages"][i]:
            index_list.append(i)

In [109]:
df.loc[index_list, "balconies"].value_counts()

balconies
Yes        3902
No_data    1140
No           21
Name: count, dtype: int64

In [110]:
df.loc[index_list, "balconies"] = df.loc[index_list, "balconies"].apply(lambda x: "Yes")

In [111]:
df["balconies"].value_counts()

balconies
Yes        4513
No_data     862
No          126
Name: count, dtype: int64

In [112]:
df = df.drop(["balcony", "balcony_area", "terrace", "loggia", "garden"], axis=1) # Removing unnecessary columns

### Column "property_condition"
The property's condition will be mapped to 10 categories.

In [113]:
df["property_condition"].value_counts(dropna=False)

property_condition
NaN                             1599
Bardzo dobry                     786
Deweloperski                     657
WYSOKI STANDARD                  336
DO WYKOŃCZENIA                   288
BARDZO WYSOKI STANDARD           242
Dobry                            221
Do remontu                       213
Do wprowadzenia                  194
Do odświeżenia                   174
Do zamieszkania                  130
Do wykończenia                   106
DOBRY                             97
Wysoki standard                   95
DO REMONTU                        74
Do generalnego remontu            41
Po generalnym remoncie            31
Idealny                           26
Do odnowienia                     26
Po remoncie                       25
DO REMONTU KAPIT.                 22
Wykończony                        19
Do adaptacji                      19
Do użytku                         17
DO ODŚWIEŻENIA                    16
Częściowo po remoncie              6
średni             

In [114]:
property_condition_dict = {"WYSOKI STANDARD": "High standard",
                           "Wysoki standard": "High standard",
                           "Idealny": "High standard",
                           "DO REMONTU": "For renovation",
                           "Do remontu": "For renovation",
                           "Do generalnego remontu": "For renovation",
                           "DO REMONTU KAPIT.": "For renovation",
                           "Budowa/remont": "For renovation",
                           "Do odnowienia": "For refreshing/ minor renovation",
                           "DO ODŚWIEŻENIA": "For refreshing/ minor renovation",
                           "DO DROBNEGO REMONTU": "For refreshing/ minor renovation",
                           "Wymaga remontu drobnego": "For refreshing/ minor renovation",
                           "Częściowo po remoncie": "For refreshing/ minor renovation",
                           "średni": "For refreshing/ minor renovation",
                           "Do odświeżenia": "For refreshing/ minor renovation",
                           "Standard": "Good standard",
                           "DOBRY": "Good standard",
                           "Dobry": "Good standard",
                           "BARDZO WYSOKI STANDARD": "Very high standard",
                           "Luksusowy": "Very high standard",
                           "Do zamieszkania": "Apartment ready to move in",
                           "Do wprowadzenia": "Apartment ready to move in",
                           "Do użytku": "Apartment ready to move in", 
                            "Wykończony": "Apartment ready to move in",
                           "Po generalnym remoncie": "After renovation",
                           "Odnowione": "After renovation",
                           "Po remoncie": "After renovation",
                           "DO WYKOŃCZENIA": "Developer condition/ to be finished",
                           "Do wykończenia": "Developer condition/ to be finished",
                            "Deweloperski": "Developer condition/ to be finished",
                           "Stan deweloperski": "Developer condition/ to be finished",
                           "BARDZO DOBRY": "Very good standard",
                           "Bardzo dobry": "Very good standard",
                           "DO ADAPTACJI": "Apartment for adaptation",
                           "Do adaptacji": "Apartment for adaptation",
                           "Bez białego montażu": "Other",
                           "Bez białego montażu i podłóg": "Other",
                           "Surowy zamknięty": "Other",
                           "Inna": "Other",
                           "Nowy": "Other"                       
}

In [115]:
df.property_condition = df.property_condition.replace(property_condition_dict)

In [116]:
df["property_condition"].value_counts(dropna=False)

property_condition
NaN                                    1599
Developer condition/ to be finished    1053
Very good standard                      787
High standard                           457
Apartment ready to move in              360
For renovation                          352
Good standard                           322
Very high standard                      243
For refreshing/ minor renovation        232
After renovation                         58
Apartment for adaptation                 24
Other                                    14
Name: count, dtype: int64

In [117]:
df["property_condition"].value_counts(dropna=False)

property_condition
NaN                                    1599
Developer condition/ to be finished    1053
Very good standard                      787
High standard                           457
Apartment ready to move in              360
For renovation                          352
Good standard                           322
Very high standard                      243
For refreshing/ minor renovation        232
After renovation                         58
Apartment for adaptation                 24
Other                                    14
Name: count, dtype: int64

The property condition will be mapped to a number between 1 and 10, where 1 is the worst condition and 10 is the best. Apartments with a property condition of "Other" will be removed.

In [118]:
property_condition_dict = {"For renovation": 1,
                           "For refreshing/ minor renovation": 2,
                           "Good standard": 3,
                           "After renovation": 4,
                           "Developer condition/ to be finished": 5,
                           "Apartment for adaptation": 6,
                           "Apartment ready to move in": 7,
                           "Very good standard": 8,
                           "High standard": 9,
                           "Very high standard": 10
                          }

In [119]:
df.property_condition = df.property_condition.map(property_condition_dict)

In [120]:
df["property_condition"].value_counts(dropna=False)

property_condition
NaN     1613
5.0     1053
8.0      787
9.0      457
7.0      360
1.0      352
3.0      322
10.0     243
2.0      232
4.0       58
6.0       24
Name: count, dtype: int64

Missing data will be filled in via KNNImputer.

In [121]:
df.property_condition = knn_imputer.fit_transform(df[["property_condition"]]) #Filling in the missing data

### Column "form_of_ownership"
The form of ownership will be mapped to 4 categories.

In [122]:
df["form_of_ownership"].value_counts(dropna=False)

form_of_ownership
NaN                                       1876
Własność                                  1769
WŁASNOŚĆ                                   934
Odrębna własność lokalu                    350
Umowa z Deweloperem                        182
SPÓŁDZIELCZE WŁASNOŚCIOWE Z KW              56
Pełna własność                              48
Spółdzielcze własnościowe                   47
SPÓŁDZIELCZE WŁASNOŚCIOWE                   40
Hipoteczne                                  35
Spółdzielcze-własnościowe                   29
Udział                                      22
Spółdzielcze-własnościowe z KW              19
Spółdzielcze + kw                           18
WSPÓŁWŁASNOŚĆ                               12
Współwłasność                                9
Spółdzielcza wł. z KW                        8
Odrębna własność                             7
Inny                                         6
Spółdzielcze wł. - księga                    5
Spółdzielcze własn. z KW                  

In [123]:
form_of_ownership_dict = {"WŁASNOŚĆ": "Ownership",
                          "Pełna własność": "Ownership",
                          "Odrębna własność lokalu": "Ownership",
                          "Odrębna własność": "Ownership",
                          "PEŁNA WŁASNOŚĆ": "Ownership",
                          "Własność hipoteczna": "Ownership",
                          "Pełna własność (hipoteczne)": "Ownership",
                          "Hipoteczne": "Ownership",
                          "Własność": "Ownership",
                          "SPÓŁDZIELCZE WŁASNOŚCIOWE Z KW": "Cooperative ownership",
                          "Spółdzielcze-własnościowe z KW": "Cooperative ownership",
                          "Spółdzielcze + kw": "Cooperative ownership",
                          "Spółdzielcza wł. z KW": "Cooperative ownership",
                          "Spółdzielcze wł. - księga": "Cooperative ownership",
                          "Spółdzielcze własn. z KW": "Cooperative ownership",
                          "Spółdzielcze z własną księga wieczystą": "Cooperative ownership",
                          "Spółdzielcze z własną księga wieczystą": "Cooperative ownership",
                          "SPÓŁDZIELCZE WŁASNOŚCIOWE": "Cooperative ownership",
                          "Spółdzielcze-własnościowe": "Cooperative ownership",
                          "Spółdzielcze": "Cooperative ownership",
                          "Spoldzielcze-wlasnosciowe": "Cooperative ownership",
                          "Spółdzielcza własnościowa": "Cooperative ownership",
                          "Spółdzielcze własnościowe prawo": "Cooperative ownership",
                          "Spółdzielcze własnościowe": "Cooperative ownership",
                          "Ekspektatywa": "Contract with developer",
                          "Umowa z Deweloperem": "Contract with developer",
                          "WSPÓŁWŁASNOŚĆ": "Share/ social housing association/ perpetual usufruct",
                          "Współwłasność": "Share/ social housing association/ perpetual usufruct",
                          "TBS": "Share/ social housing association/ perpetual usufruct",
                          "Użytkowanie wieczyste": "Share/ social housing association/ perpetual usufruct",
                          "Udział": "Share/ social housing association/ perpetual usufruct",
                          "Inny": "Other",
                          "Inne": "Other",
                          "INNA": "Other",
                         }

In [124]:
df.form_of_ownership = df.form_of_ownership.replace(form_of_ownership_dict)

The form of ownership will be mapped to numbers between 1 and 4, where 1 is the worst form and 4 is the best. Apartments with the "Other" form of ownership will be removed.

In [125]:
df["form_of_ownership"].value_counts(dropna=False)

form_of_ownership
Ownership                                                3151
NaN                                                      1876
Cooperative ownership                                     235
Contract with developer                                   183
Share/ social housing association/ perpetual usufruct      47
Other                                                       9
Name: count, dtype: int64

In [126]:
form_of_ownership_dict = {"Share/ social housing association/ perpetual usufruct": 1,
                          "Cooperative ownership": 2,
                          "Contract with developer": 3,
                          "Ownership": 4
                         }

In [127]:
df.form_of_ownership = df.form_of_ownership.map(form_of_ownership_dict)

In [128]:
df["form_of_ownership"].value_counts(dropna=False)

form_of_ownership
4.0    3151
NaN    1885
2.0     235
3.0     183
1.0      47
Name: count, dtype: int64

Missing data will be filled in via KNNImputer.

In [129]:
df.form_of_ownership = knn_imputer.fit_transform(df[["form_of_ownership"]]) #Filling in the missing data

### Column "advantages"
The "advantages" column lists other apartment features that may also impact the price. Among these features, the following were selected as significant: parking space, underground parking, basement, storage unit, lift, smart home, and air conditioning. New columns were created for these features, indicating whether the apartment has a given feature. Features: parking space and underground parking are combined in one column: "parking." Features: basement and storage unit are combined in one column: "basement_storage_unit".

In [130]:
df.advantages.value_counts()

advantages
[]                                                                                                                                                                                                                                             175
['dla osób z niepełnosprawnością', 'komórka lokatorska', 'winda', 'balkon', 'kuchnia otwarta', 'miejsce parkingowe', 'osiedle zamknięte', 'parking podziemny']                                                                                 117
['balkon', 'kuchnia otwarta']                                                                                                                                                                                                                   71
['balkon', 'kuchnia osobna', 'miejsce parkingowe', 'parking podziemny']                                                                                                                                                                         68
['winda', 'balkon

In [131]:
parking_index = []
parking_list = ['miejsce parkingowe', 'parking podziemny']
for i in range(len(df["advantages"])):
    for j in parking_list:
        if j in df["advantages"][i]:
            parking_index.append(i)

In [132]:
df["parking"] = "No_data"

In [133]:
df.loc[parking_index, "parking"] = df.loc[parking_index, "parking"].replace({"No_data": "Yes"})

In [134]:
basement_index = []
basement_list = ['komórka lokatorska', 'piwnica']
for i in range(len(df["advantages"])):
    for j in basement_list:
        if j in df["advantages"][i]:
            basement_index.append(i)

In [135]:
df["basement_storage_unit"] = "No_data"

In [136]:
df.loc[basement_index, "basement_storage_unit"] = df.loc[basement_index, "basement_storage_unit"].replace({"No_data": "Yes"})

In [137]:
list_advantages = ['winda',  
                   'inteligentny dom',
                   'klimatyzacja'
                  ]
lift = []
smart_home = []
air_conditioning = []
lists_index = [lift,
               smart_home,
               air_conditioning
              ]

In [138]:
for j in range(len(list_advantages)):
    for i in range(len(df["advantages"])):
        if list_advantages[j] in df["advantages"][i]:
            lists_index[j].append(i)
    df[list_advantages[j]] = "No_data"
    df.loc[lists_index[j], list_advantages[j]] = df.loc[lists_index[j], list_advantages[j]].replace({"No_data": "Yes"})

In [139]:
df = df.rename(columns={"winda":"lift",
                        "inteligentny dom": "smart home", 
                        "klimatyzacja": "air conditioning"
})

In [140]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5501 entries, 0 to 5500
Data columns (total 22 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   price                  5501 non-null   int64  
 1   rooms                  5501 non-null   int32  
 2   area                   5501 non-null   float64
 3   market                 5501 non-null   object 
 4   building_type          5501 non-null   object 
 5   building_material      5501 non-null   object 
 6   year_built             5501 non-null   float64
 7   heating                5501 non-null   object 
 8   kitchen_type           5501 non-null   object 
 9   property_condition     5501 non-null   float64
 10  form_of_ownership      5501 non-null   float64
 11  advantages             5501 non-null   object 
 12  link                   5501 non-null   object 
 13  district_result        5501 non-null   object 
 14  distance_from_center   5501 non-null   float64
 15  floo

### Column "rooms_to_area_ratio"
A new column, "rooms_to_area_ratio," will be created, which will include the ratio of the number of rooms to the apartment's area. This can be important when training the model.

In [141]:
df["rooms_to_area_ratio"] = df.rooms/df.area

In [142]:
df = df.drop(["advantages", "link"], axis=1) # Removing unnecessary columns

### Saving a data frame to CSV

In [143]:
df.to_csv("flats_result_set1.csv", index=False)